In [17]:
import numpy as np
import pandas as pd
from gensim.models import Doc2Vec
from gensim.models.doc2vec import TaggedDocument
from nltk import word_tokenize

In [18]:
train_data=pd.read_csv("DataSet/Train.csv")
test_data=pd.read_csv('DataSet/Test.csv')


In [19]:
result_data=pd.read_csv('DataSet/Results.csv')

In [20]:
train_data.head(5)

question  \
0                                Meals can be served   
1           It can be inferred from the passage that   
2     The author called Tommy 's parents in order to   
3           It can be inferred from the passage that   
4  How can we deal with snake wounds according to...   

                                         answer_text  \
0                             in rooms at 9:00 p. m.   
1  The local government can deal with the problem...   
2         help them realize their influence on Tommy   
3       the writer is not very willing to use idioms   
4                        Stay calm and do n't move .   

                                          distractor  
0  'outside the room at 3:00 p. m.', 'in the dini...  
1  'If some tragedies occur again ', ' relevant d...  
2  'blame Tommy for his failing grades', 'blame T...  
3  'idioms are the most important part in a langu...  
4          'Cut the wound and suck the poison out .'

In [21]:
# text cleaning 
import re
punctuations = '''!()-[]{};:'"\,<>./?@#$%^&*_~'''
def sent_clean(my_str):
    my_str=my_str.lower()
    my_str= re.sub("n't", "not",my_str )
    my_str = re.sub("'s", "", my_str)
    my_str = re.sub("'ll", "", my_str)
    my_str=re.sub("p.m","pm",my_str)
    my_str=re.sub("a.m","am",my_str)
    
    no_punct = ""
    for char in my_str:
        if char not in punctuations:
            no_punct = no_punct + char
    return(no_punct)

In [22]:
# getting each sentence from distractors and appending in a list
distractors=[]
for i in train_data['distractor']:
    j=i.split(',')
    for k in j:
        l=sent_clean(k)
        distractors.append(l)
    

In [23]:
# applyig sent_clean function on our data sets
train_data['question']=train_data['question'].apply(sent_clean)
# test_data['answer_text']=test_data['answer_text'].apply(sent_clean)
# train_data['answer_text']=train_data['answer_text'].apply(sent_clean)
result_data_answer=result_data['answer_text'].apply(sent_clean)
test_data_answer=test_data['answer_text'].apply(sent_clean)
train_data_answer=train_data['answer_text'].apply(sent_clean)

In [24]:
class TaggedDocumentIterator(object):
    def __init__(self, doc_list, labels_list):
        self.labels_list = labels_list
        self.doc_list = doc_list
    def __iter__(self):
        for idx, doc in enumerate(self.doc_list):
            yield TaggedDocument(words=doc.split(), tags=[self.labels_list[idx]])

            

dt = list(train_data_answer)
len(dt)
dt.extend(distractors)
len(dt)
total_indx=len(dt)
docLabels = list(range(total_indx))
len(docLabels)
sentences = TaggedDocumentIterator(dt, docLabels)


model = Doc2Vec(size=100, window=10, min_count=5, workers=11,alpha=0.025, iter=20)
model.build_vocab(sentences)
model.train(sentences,total_examples=model.corpus_count, epochs=model.iter)

C:\Users\user\Anaconda3\lib\site-packages\gensim\models\doc2vec.py:362: UserWarning: The parameter `iter` is deprecated, will be removed in 4.0.0, use `epochs` instead.
  warnings.warn("The parameter `iter` is deprecated, will be removed in 4.0.0, use `epochs` instead.")
C:\Users\user\Anaconda3\lib\site-packages\gensim\models\doc2vec.py:366: UserWarning: The parameter `size` is deprecated, will be removed in 4.0.0, use `vector_size` instead.
  warnings.warn("The parameter `size` is deprecated, will be removed in 4.0.0, use `vector_size` instead.")
C:\Users\user\Anaconda3\lib\site-packages\ipykernel_launcher.py:23: DeprecationWarning: Call to deprecated `iter` (Attribute will be removed in 4.0.0, use self.epochs instead).


In [25]:
type(sentences)

__main__.TaggedDocumentIterator

In [26]:
# getting text back from vector output
def get_distractor(strng):
    tokens = strng.split()
    new_vector = model.infer_vector(tokens)
    most_similar_docs = []
    for d in model.docvecs.most_similar([new_vector],topn=3):
        most_similar_docs.append(dt[d[0]])
    return(most_similar_docs)

In [27]:
#test_data['answer_text']=test_data['answer_text'].apply(sent_clean)

In [28]:
#result_data['answer_text']=result_data['answer_text'].apply(sent_clean)

In [29]:
result_distractors=[]
for i in result_data_answer:
    distrct=get_distractor(i)
    for et in distrct:
        if et=='' or et==' ':
            dindx=distrct.index(et)
            distrct[dindx]=i
    result_distractors.append(distrct)
    
        
result_data['distractor']=result_distractors 

In [30]:
test_distractors=[]
for i in test_data_answer:
    distrct=get_distractor(i)
    for et in distrct:
        #print(et,"\n")
        if et=='' or et==' ':
            dindx=distrct.index(et)
            distrct[dindx]=i
    test_distractors.append(distrct)

In [31]:
test_data['distractor']=test_distractors
test_data.sample(7)

question  \
3881  By reading weather maps , students majoring in...   
5391  If we put food in a blue box and do this every...   
1078               What can we infer from the passage ?   
8585  What 's the floodplain death adder 's method t...   
9732                 Children may be more rebellious if   
35    Which of the following is TRUE about homeschoo...   
7757                   Which of the following is TRUE ?   

                                            answer_text  \
3881  obtain data on atmospheric conditions over a w...   
5391                           the blue box to get food   
1078  The machine can help raise awareness of lackin...   
8585  They inject poison on the preys and wait for t...   
9732       they know parents think risktaking is normal   
35    Some parents have to homeschool their children...   
7757  Angel should show her parents that she is a re...   

                                             distractor  
3881  [something about natural body rhythm ,  contro...  
5391  [they hoped to get supplies of food and water,...  
1078  [help the needy people in the world,  to help ...  
8585  [ they burn their hand on the stove and stick ...  
9732  [ know the differences between chinese and eng...  
35    [when her parents brought back home some cds ,...  
7757  [ noah was born with his parents  dream of his...

In [32]:
# function to get cosine similarity score between test data answer and distractors

# packages
from sklearn.feature_extraction.text import CountVectorizer
from scipy.spatial import distance
allsentences = dt
allsentences.extend(list(test_data_answer))
# text to vector
vectorizer = CountVectorizer()
all_sentences_to_vector = vectorizer.fit_transform(allsentences)

def cosine_distance_countvectorizer_method(s1, s2):
    
    text_to_vector_v1=vectorizer.transform([s1]).toarray().tolist()
    text_to_vector_v2=vectorizer.transform([s2]).toarray().tolist()
    #text_to_vector_v1 = all_sentences_to_vector.toarray()[0].tolist()
    #text_to_vector_v2 = all_sentences_to_vector.toarray()[1].tolist()
    
    # distance of similarity
    cosine = distance.cosine(text_to_vector_v1, text_to_vector_v2)
    print('Similarity of two sentences are equal to ',round((1-cosine)*100,2),'%')
    return (round((1-cosine)*100,2))



In [33]:
# def cosine_score(dff,df_dstr):
#     cosine_scores=[]
#     for i in range(len(dff['answer_text'])):
#         rvw=dff['answer_text'][i]
#         temp=[]
#         for j in df_dstr[i]:
#             scr=cosine_distance_countvectorizer_method(rvw,j)
#             temp.append(scr)
#         cosine_scores.append(temp)
#     return(cosine_scores)
            

In [34]:
def cosine_score(dff,df_dstr):
    cosine_scores=[]
    for i in range(len(dff)):
        rvw=dff[i]
        temp=[]
        for j in df_dstr[i]:
            scr=cosine_distance_countvectorizer_method(rvw,j)
            temp.append(scr)
        cosine_scores.append(temp)
    return(cosine_scores)
            

In [35]:
test_distractor_scores=cosine_score(test_data_answer,test_distractors)
result_distractor_scores=cosine_score(result_data_answer,result_distractors)

Similarity of two sentences are equal to  90.0 %
Similarity of two sentences are equal to  12.91 %
Similarity of two sentences are equal to  38.14 %
Similarity of two sentences are equal to  18.26 %
Similarity of two sentences are equal to  16.67 %
Similarity of two sentences are equal to  35.36 %
Similarity of two sentences are equal to  29.28 %
Similarity of two sentences are equal to  20.97 %
Similarity of two sentences are equal to  30.86 %
Similarity of two sentences are equal to  34.3 %
Similarity of two sentences are equal to  33.33 %
Similarity of two sentences are equal to  31.98 %
Similarity of two sentences are equal to  55.56 %
Similarity of two sentences are equal to  52.7 %
Similarity of two sentences are equal to  27.22 %
Similarity of two sentences are equal to  19.61 %
Similarity of two sentences are equal to  25.09 %
Similarity of two sentences are equal to  22.65 %
Similarity of two sentences are equal to  37.5 %
Similarity of two sentences are equal to  31.62 %
Simi

Similarity of two sentences are equal to  43.03 %
Similarity of two sentences are equal to  29.42 %
Similarity of two sentences are equal to  18.49 %
Similarity of two sentences are equal to  36.98 %
Similarity of two sentences are equal to  25.72 %
Similarity of two sentences are equal to  21.0 %
Similarity of two sentences are equal to  8.57 %
Similarity of two sentences are equal to  20.97 %
Similarity of two sentences are equal to  24.81 %
Similarity of two sentences are equal to  16.01 %
Similarity of two sentences are equal to  0.0 %
Similarity of two sentences are equal to  0.0 %
Similarity of two sentences are equal to  0.0 %
Similarity of two sentences are equal to  25.2 %
Similarity of two sentences are equal to  37.8 %
Similarity of two sentences are equal to  44.72 %
Similarity of two sentences are equal to  15.43 %
Similarity of two sentences are equal to  28.57 %
Similarity of two sentences are equal to  16.9 %
Similarity of two sentences are equal to  33.33 %
Similarity 

Similarity of two sentences are equal to  0.0 %
Similarity of two sentences are equal to  18.26 %
Similarity of two sentences are equal to  13.61 %
Similarity of two sentences are equal to  30.86 %
Similarity of two sentences are equal to  33.33 %
Similarity of two sentences are equal to  40.82 %
Similarity of two sentences are equal to  38.73 %
Similarity of two sentences are equal to  40.82 %
Similarity of two sentences are equal to  14.91 %
Similarity of two sentences are equal to  11.11 %
Similarity of two sentences are equal to  47.14 %
Similarity of two sentences are equal to  40.82 %
Similarity of two sentences are equal to  38.49 %
Similarity of two sentences are equal to  37.5 %
Similarity of two sentences are equal to  21.32 %
Similarity of two sentences are equal to  37.5 %
Similarity of two sentences are equal to  22.36 %
Similarity of two sentences are equal to  11.18 %
Similarity of two sentences are equal to  30.0 %
Similarity of two sentences are equal to  25.82 %
Simil

Similarity of two sentences are equal to  0.0 %
Similarity of two sentences are equal to  22.22 %
Similarity of two sentences are equal to  40.82 %
Similarity of two sentences are equal to  27.22 %
Similarity of two sentences are equal to  24.25 %
Similarity of two sentences are equal to  21.08 %
Similarity of two sentences are equal to  13.61 %
Similarity of two sentences are equal to  57.74 %
Similarity of two sentences are equal to  57.74 %
Similarity of two sentences are equal to  31.62 %
Similarity of two sentences are equal to  22.36 %
Similarity of two sentences are equal to  33.54 %
Similarity of two sentences are equal to  35.36 %
Similarity of two sentences are equal to  22.36 %
Similarity of two sentences are equal to  45.64 %
Similarity of two sentences are equal to  50.0 %
Similarity of two sentences are equal to  25.82 %
Similarity of two sentences are equal to  16.9 %
Similarity of two sentences are equal to  25.82 %
Similarity of two sentences are equal to  78.33 %
Simi

Similarity of two sentences are equal to  22.22 %
Similarity of two sentences are equal to  20.1 %
Similarity of two sentences are equal to  10.05 %
Similarity of two sentences are equal to  0.0 %
Similarity of two sentences are equal to  0.0 %
Similarity of two sentences are equal to  0.0 %
Similarity of two sentences are equal to  42.43 %
Similarity of two sentences are equal to  25.82 %
Similarity of two sentences are equal to  18.26 %
Similarity of two sentences are equal to  0.0 %
Similarity of two sentences are equal to  30.86 %
Similarity of two sentences are equal to  16.9 %
Similarity of two sentences are equal to  30.86 %
Similarity of two sentences are equal to  20.41 %
Similarity of two sentences are equal to  20.41 %
Similarity of two sentences are equal to  18.26 %
Similarity of two sentences are equal to  22.36 %
Similarity of two sentences are equal to  11.18 %
Similarity of two sentences are equal to  14.43 %
Similarity of two sentences are equal to  16.67 %
Similarity

...

Similarity of two sentences are equal to  26.73 %
Similarity of two sentences are equal to  13.36 %
Similarity of two sentences are equal to  50.0 %
Similarity of two sentences are equal to  28.87 %
Similarity of two sentences are equal to  50.0 %
Similarity of two sentences are equal to  47.81 %
Similarity of two sentences are equal to  20.0 %
Similarity of two sentences are equal to  33.54 %
Similarity of two sentences are equal to  13.61 %
Similarity of two sentences are equal to  27.22 %
Similarity of two sentences are equal to  33.33 %
Similarity of two sentences are equal to  30.86 %
Similarity of two sentences are equal to  0.0 %
Similarity of two sentences are equal to  0.0 %
Similarity of two sentences are equal to  23.57 %
Similarity of two sentences are equal to  16.67 %
Similarity of two sentences are equal to  23.57 %
Similarity of two sentences are equal to  0.0 %
Similarity of two sentences are equal to  19.25 %
Similarity of two sentences are equal to  8.33 %
Similarity

Similarity of two sentences are equal to  11.32 %
Similarity of two sentences are equal to  8.77 %
Similarity of two sentences are equal to  9.81 %
Similarity of two sentences are equal to  12.4 %
Similarity of two sentences are equal to  23.57 %
Similarity of two sentences are equal to  20.41 %
Similarity of two sentences are equal to  21.82 %
Similarity of two sentences are equal to  25.2 %
Similarity of two sentences are equal to  8.61 %
Similarity of two sentences are equal to  23.57 %
Similarity of two sentences are equal to  15.81 %
Similarity of two sentences are equal to  16.9 %
Similarity of two sentences are equal to  22.36 %
Similarity of two sentences are equal to  21.82 %
Similarity of two sentences are equal to  28.87 %
Similarity of two sentences are equal to  28.87 %
Similarity of two sentences are equal to  33.33 %
Similarity of two sentences are equal to  0.0 %
Similarity of two sentences are equal to  44.72 %
Similarity of two sentences are equal to  16.9 %
Similarit

Similarity of two sentences are equal to  26.97 %
Similarity of two sentences are equal to  45.58 %
Similarity of two sentences are equal to  20.1 %
Similarity of two sentences are equal to  19.07 %
Similarity of two sentences are equal to  18.26 %
Similarity of two sentences are equal to  10.54 %
Similarity of two sentences are equal to  0.0 %
Similarity of two sentences are equal to  0.0 %
Similarity of two sentences are equal to  0.0 %
Similarity of two sentences are equal to  0.0 %
Similarity of two sentences are equal to  35.86 %
Similarity of two sentences are equal to  10.48 %
Similarity of two sentences are equal to  47.81 %
Similarity of two sentences are equal to  8.36 %
Similarity of two sentences are equal to  9.53 %
Similarity of two sentences are equal to  8.36 %
Similarity of two sentences are equal to  28.28 %
Similarity of two sentences are equal to  33.81 %
Similarity of two sentences are equal to  14.91 %
Similarity of two sentences are equal to  33.33 %
Similarity o

Similarity of two sentences are equal to  16.67 %
Similarity of two sentences are equal to  29.28 %
Similarity of two sentences are equal to  36.51 %
Similarity of two sentences are equal to  40.0 %
Similarity of two sentences are equal to  50.0 %
Similarity of two sentences are equal to  47.14 %
Similarity of two sentences are equal to  22.22 %
Similarity of two sentences are equal to  16.9 %
Similarity of two sentences are equal to  16.9 %
Similarity of two sentences are equal to  0.0 %
Similarity of two sentences are equal to  14.91 %
Similarity of two sentences are equal to  16.9 %
Similarity of two sentences are equal to  40.0 %
Similarity of two sentences are equal to  14.29 %
Similarity of two sentences are equal to  13.36 %
Similarity of two sentences are equal to  11.95 %
Similarity of two sentences are equal to  27.74 %
Similarity of two sentences are equal to  49.61 %
Similarity of two sentences are equal to  24.81 %
Similarity of two sentences are equal to  16.9 %
Similarit

Similarity of two sentences are equal to  22.36 %
Similarity of two sentences are equal to  0.0 %
Similarity of two sentences are equal to  0.0 %
Similarity of two sentences are equal to  28.87 %
Similarity of two sentences are equal to  14.43 %
Similarity of two sentences are equal to  15.43 %
Similarity of two sentences are equal to  12.31 %
Similarity of two sentences are equal to  60.68 %
Similarity of two sentences are equal to  0.0 %
Similarity of two sentences are equal to  22.36 %
Similarity of two sentences are equal to  0.0 %
Similarity of two sentences are equal to  13.36 %
Similarity of two sentences are equal to  12.6 %
Similarity of two sentences are equal to  25.2 %
Similarity of two sentences are equal to  30.15 %
Similarity of two sentences are equal to  18.49 %
Similarity of two sentences are equal to  39.22 %
Similarity of two sentences are equal to  21.32 %
Similarity of two sentences are equal to  11.79 %
Similarity of two sentences are equal to  30.15 %
Similarity

In [36]:
test_data['cosine score %']=test_distractor_scores
#result_data['cosine score %']=result_distractor_scores

In [37]:
# test data with distactors and cosine scores
test_data.head(10)

question  \
0                What 'S the main idea of the text ?   
1  In the summer high season , Finland does nt se...   
2  If you want to apply for Chinese Business Inte...   
3  That afternoon , the boy 's clothes were dry b...   
4    Which of the following statements is NOT true ?   
5  The problem of " lock - in " can be dangerous ...   
6                        The passage is mainly about   
7               Which of the following in not true ?   
8                   What should you do at mealtime ?   
9  The part of " Only you can make a card like th...   

                                         answer_text  \
0  The lack of career -- based courses in US high...   
1                            the sun is out at night   
2               have to get confirmed at least twice   
3            nobody made room for him in the water .   
4  There are twelve countries in the World Wildli...   
5  it may make it difficult for customers to reco...   
6      how Billy made blueberry juice with his uncle   
7           The snail 's teeth ca n't be worn out ..   
8          Eat the food your host family gives you .   
9                  how to make a meaningful DIY card   

                                          distractor         cosine score %  
0  [the lack of career  based education in us hig...   [90.0, 12.91, 38.14]  
1  [watch out your credit cards ,  use their fing...  [18.26, 16.67, 35.36]  
2  [he went to the cupboard to get the bottle by ...  [29.28, 20.97, 30.86]  
3  [ the writer thought the son wasted water duri...   [34.3, 33.33, 31.98]  
4  [there are more men than women in the world, o...   [55.56, 52.7, 27.22]  
5  [  the fishermen would have nothing for their ...  [19.61, 25.09, 22.65]  
6  [how darwin made his voyage to south america, ...   [37.5, 31.62, 28.87]  
7  [ to wash hands often ,  keep off junk food , ...        [0.0, 0.0, 0.0]  
8  [  you do exist , giving means you will lack m...  [20.41, 14.43, 14.43]  
9  [how to have a bank card,  how how to wear a s...   [54.77, 43.3, 16.67]

In [38]:
result_data

question  \
0                    What 'S the main idea of the text ?   
1      In the summer high season , Finland does nt se...   
2      If you want to apply for Chinese Business Inte...   
3      That afternoon , the boy 's clothes were dry b...   
4        Which of the following statements is NOT true ?   
...                                                  ...   
13495   Who helped set up the first company in America ?   
13496  Which of the following statements is True acco...   
13497                            What is the main idea ?   
13498                      From the passage we know that   
13499  What does the circus think of its performing a...   

                                             answer_text  \
0      The lack of career -- based courses in US high...   
1                                the sun is out at night   
2                   have to get confirmed at least twice   
3                nobody made room for him in the water .   
4      There are twelve countries in the World Wildli...   
...                                                  ...   
13495                                Benjamin Franklin .   
13496  None of the soldiers who got on the train for ...   
13497                     Every person should exercise .   
13498                not everybody can buy such a fridge   
13499         They are helpful in saving their species .   

                                              distractor  
0      [dictionaries are very useful to us , it guara...  
1      [amovie about the story is coming out ,   but ...  
2      [ get new ideas, germs can get into your body ...  
3      [ the water carried him across it ,  nobody ne...  
4      [they do not feel they belong to the world of ...  
...                                                  ...  
13495  [fresh water and sea water,  in a hotel dining...  
13496  [ the people who do not work on the census wil...  
13497  [ women should work longer than men , children...  
13498  [people suffering earthquakes often should buy...  
13499  [both banks and linneaus devoted their whole l...  

[13500 rows x 3 columns]

In [39]:
# converting the prediction in desired format
for i in range(len(result_data['distractor'])):
    tx=result_data['distractor'][i]
    tx=re.sub("\[",'',str(tx))
    tx=re.sub("\]",'',tx)
    result_data['distractor'][i]=tx

In [40]:
# converting the prediction in desired format
for i in range(len(test_data['distractor'])):
    tx=test_data['distractor'][i]
    tx=re.sub("\[",'',str(tx))
    tx=re.sub("\]",'',tx)
    test_data['distractor'][i]=tx

In [41]:
# saving prediction for test data in test.csv
test_data.to_csv('DataSet/Test.csv',index=False)

In [42]:
# Saving the final result to Results.csv
result_data.to_csv('DataSet/Results.csv',index=False)
result_data.to_csv('Results.csv',index=False)

In [43]:
result=pd.read_csv('Results.csv')

In [44]:
len(result)

13500

In [45]:
result.head()

question  \
0                What 'S the main idea of the text ?   
1  In the summer high season , Finland does nt se...   
2  If you want to apply for Chinese Business Inte...   
3  That afternoon , the boy 's clothes were dry b...   
4    Which of the following statements is NOT true ?   

                                         answer_text  \
0  The lack of career -- based courses in US high...   
1                            the sun is out at night   
2               have to get confirmed at least twice   
3            nobody made room for him in the water .   
4  There are twelve countries in the World Wildli...   

                                          distractor  
0  'dictionaries are very useful to us ', 'it gua...  
1  'amovie about the story is coming out ', '  bu...  
2  ' get new ideas', 'germs can get into your bod...  
3  ' the water carried him across it ', ' nobody ...  
4  'they do not feel they belong to the world of ...

In [46]:
#cosine similarity between answer and distractors of result data
result_df=result
result_df['cosine similarity %']=result_distractor_scores
result_df.sample(10)

question  \
13431           According to the passage , the new study   
13258             In the author 's opinion , the speaker   
1639   Quick movements by a person trapped in quicksa...   
6277      Who is the advertisement mainly intended for ?   
3106   We know a shy and lower -- ranking dog licks t...   
4412   If you choose Half Day Trip , how much time sh...   
11554  Youth volunteers from Beijing University went ...   
4836          What can we learn about the Velib scheme ?   
4681    Why does the author compare herself to flowers ?   
10727                From the passage , we can know that   

                                             answer_text  \
13431  has shown that our understanding of numbers is...   
13258  had made the language problems of the students...   
1639                make the same sand yield temporarily   
6277            People who try to improve their health .   
3106                                 show he is friendly   
4412                                     3.5 - 4 hours .   
11554                       show their love for the aged   
4836             It owns more stations than the subway .   
4681   Because she can live in any place that is righ...   
10727  rock and roll music probably came from African...   

                                              distractor  \
13431  'the internet has reduced our chances of getti...   
13258  'because korea wants to make students become m...   
1639   'make the best of what they have', 'make drawi...   
6277   ' who can drink energy drinks ', ' according t...   
3106   'be polite and friendly', 'to show that cupcak...   
4412   'twelve hours', ' pecial hours on weekdays', '...   
11554  'obese smokers are less likely to suffer from ...   
4836   'the tower of london', 'it is the biggest buil...   
4681   'warn that man must not destroy forests any mo...   
10727  'rock music developed mainly from the interact...   

         cosine similarity %  
13431   [39.28, 14.91, 8.33]  
13258   [8.33, 22.36, 82.16]  
1639   [30.86, 46.29, 24.62]  
6277      [16.9, 37.8, 16.9]  
3106     [25.0, 25.0, 20.41]  
4412     [50.0, 35.36, 50.0]  
11554    [0.0, 20.41, 23.57]  
4836    [18.9, 35.86, 34.19]  
4681   [19.25, 16.01, 36.51]  
10727  [57.74, 43.64, 18.46]

In [47]:
####################################